### Aether Satellites 

Aether satellites allow you to interact with OKAPI:Aether, more specifically for services related to satellite operations. This page provides illustrated examples to help you get started. We first import dependencies and declare variables which will be useful for our use case. The test data can be downloaded <a href="../testdata/aether_satellites_api.zip" download>here</a>, while the notebook itself may be fetched <a href="./aether_satellites.ipynb" download>here</a>.

In [1]:
import json
import os
from okapi_aether_sdk.error import ClientError
from okapi_aether_sdk.aether_satellites_api import AetherSatellitesApi

# Ensure that the .env file is populated with the required entries for authentication
aether_api = AetherSatellitesApi()
aether_api.login()

# The below code is used to load data from a repository to illustrate the use of the Aether Satellites API.
here = globals()['_dh'][0]
testdata = here / "testdata" / "aether_satellites_api"



#### Uploading satellite to OKAPI:Aether

This is the most basic operation to be performed for many interactions with OKAPI:Aether. It consists in the upload of a satellite to the system. As simple as this step is, it is crucial for many services of OKAPI:Aether, for example as outlined in [Aether Services](aether_services.ipynb). The format for a satellite dictionary is as outlined [here](https://okapiorbits.space/api-doc/#tag/developers/paths/~1satellites/post).

In [2]:
with open(os.path.join(testdata, "satellites_data.json"), "r") as fp:
    request = json.load(fp)
satellite = aether_api.add_satellite(request)

#### Fetching a satellite from OKAPI:Aether

In order to update or see a satellite's information as stored in OKAPI:Aether, it is possible to use the `get_satellite` method. Below, we use this method to retrieve the satellite we just added to the system, which allows us to verify everything went smoothly with the upload.

In [3]:
satellite = aether_api.get_satellite(satellite_id=satellite["satellite_id"])
print("Accepted collision probability for the inserted satellite: "
      f"{satellite['accepted_collision_probability']}")

Accepted collision probability for the inserted satellite: 0.0001


#### Modify a satellite in OKAPI:Aether

After retrieving the satellite, it is possible for the user to update/modify values. This is done with the `change_satellite` method. Below, we modify the accepted collision probability. 

In [4]:
satellite["accepted_collision_probability"] = 5e-4
satellite = aether_api.change_satellite(satellite)
print("Accepted collision probability for the modified satellite: "
      f"{satellite['accepted_collision_probability']}")

Accepted collision probability for the modified satellite: 0.0005


#### Retrieve OEMs for a satellite

For a given satellite, it is possible to retrieve ephemerides in various formats from OKAPI:Aether. In the example herafter, we extract the OEMs (in this case, only one) for the satellite we just created. Note that this requires the addition of ephemerides for the object, using the `add_ephemerides` method presented in [Aether Services](aether_services.ipynb). For the sake of this example, the OEM has already been uploaded.

In [5]:
oems = aether_api.get_satellite_oems(satellite["satellite_id"])
print(f"{len(oems)} OEM(s) retrieved for satellite with satellite_id "
      f"{satellite['satellite_id']}")

1 OEM(s) retrieved for satellite with satellite_id 9ad0184e-047e-4fbc-9e11-99b3171351b0


#### Upload a CDM for an asset in OKAPI:Aether

This service allows the user to upload a CDM to OKAPI:Aether. The format required for the CDM is as shown [here](https://okapiorbits.space/api-doc/#tag/developers/paths/~1cdms~1requests/post).

In [6]:
with open(os.path.join(testdata, "upload_cdm_data.json"), "r") as fp:
    cdm_dictionary = json.load(fp)
cdm_id = aether_api.upload_cdm(cdm_dictionary)
cdm_upload_result = aether_api.get_upload_cdm_results(cdm_id)
print(cdm_upload_result["status"]["text"])

No result data there yet.


#### Upload a maneuver plan 

This service enables the user to upload a maneuver plan for a satellite. The maneuver plan format is as shown [here](https://okapiorbits.space/api-doc/#tag/developers/operation/createManeuverPlan).

In [7]:
with open(os.path.join(testdata, "maneuver_plan.json"), "r") as fp:
    maneuver_plan = json.load(fp)
maneuver_plan["satellite_id"] = satellite["satellite_id"]
maneuver_plan = aether_api.add_maneuver_plan(maneuver_plan)

#### Delete a satellite from OKAPI:Aether

It is also possible for the user to delete an asset from OKAPI:Aether. In this example, we delete the satellite that was created in this example.

In [8]:
satellite = aether_api.delete_satellite(satellite["satellite_id"])
# Verify proper deletion of the satellite
try:
    satellite = aether_api.get_satellite(satellite_id=satellite["satellite_id"])
except ClientError:
    print("As expected, the satellite cannot be retrieved")

As expected, the satellite cannot be retrieved
